# Compute expected lifespan from the regression outputs on the no-disability subsample

### Import regression outputs for the 5 specifications 

In [1]:
import pandas as pd
import numpy as np
from itertools import product

df = pd.read_csv('../raw_data/output2_clean.csv', sep=',')

df2=df.transpose()
df2.columns = df2.iloc[0]
df2.drop(df2.index[0], inplace=True)
df=df2
df.index=df.index.str.replace('_t:','')
df.index=df.index.str.replace('/:','')
columns_to_convert = ['b1', 'b2', 'b3','b4','b5']  # Specify the columns you want to convert
for column in columns_to_convert:
    df[column] = df[column].astype(float)
    
df

_t:model         b1       se1        b2       se2        b3       se3  \
_cons      0.006520   0.00009  0.004623  0.000069  0.005781  0.000092   
gamma      0.115084  0.000673  0.117523  0.000674  0.118200  0.000675   
60.AC      1.146501  0.011945  1.205047  0.012586  1.163559  0.012249   
61.AC      1.077483  0.014162  1.110666  0.014604  1.086397  0.014335   
62.AC      1.071859  0.016001  1.113782  0.016638  1.091194  0.016339   
63.AC      1.046495  0.016953  1.092336  0.017709  1.075804  0.017473   
64.AC      1.085293  0.017948  1.130433  0.018706  1.118516  0.018533   
65b.AC     1.000000         .  1.000000         .  1.000000         .   
1926.coh   1.240706  0.017164  1.194310  0.016522  1.179410  0.016329   
1930.coh   1.135611    0.0146  1.108537  0.014252  1.105171  0.014212   
1935.coh   1.031933  0.013364  1.024934  0.013274  1.027327  0.013306   
1940b.coh  1.000000         .  1.000000         .  1.000000         .   
1945.coh   0.954406  0.015377  0.964071  0.015534  0.962177  0.015503   
1950.coh   0.915315  0.023033  0.928924  0.023379  0.924640  0.023273   
0b.SEX          NaN       NaN  1.000000         .  1.000000         .   
1.SEX           NaN       NaN  1.675294  0.012987  1.769288  0.014065   
0b.imm_d        NaN       NaN       NaN       NaN  1.000000         .   
1.imm_d         NaN       NaN       NaN       NaN  0.760002  0.010962   
0b.mrt          NaN       NaN       NaN       NaN  1.000000         .   
1.mrt           NaN       NaN       NaN       NaN  0.750012  0.006549   
2.mrt           NaN       NaN       NaN       NaN  0.956183  0.027754   
1.p_lvl         NaN       NaN       NaN       NaN       NaN       NaN   
2.p_lvl         NaN       NaN       NaN       NaN       NaN       NaN   
3b.p_lvl        NaN       NaN       NaN       NaN       NaN       NaN   
4.p_lvl         NaN       NaN       NaN       NaN       NaN       NaN   
5.p_lvl         NaN       NaN       NaN       NaN       NaN       NaN   
0.pp_lvl        NaN       NaN       NaN       NaN       NaN       NaN   
1.pp_lvl        NaN       NaN       NaN       NaN       NaN       NaN   
2.pp_lvl        NaN       NaN       NaN       NaN       NaN       NaN   
3b.pp_lvl       NaN       NaN       NaN       NaN       NaN       NaN   
4.pp_lvl        NaN       NaN       NaN       NaN       NaN       NaN   
5.pp_lvl        NaN       NaN       NaN       NaN       NaN       NaN   

_t:model         b4       se4        b5       se5         N   N_fail  
_cons      0.005257  0.000096  0.004600  0.000093  307055.0  72235.0  
gamma      0.118690  0.000675  0.120539  0.000676       NaN      NaN  
60.AC      1.163952  0.012262  1.190298  0.012613       NaN      NaN  
61.AC      1.082739  0.014289  1.101010  0.014552       NaN      NaN  
62.AC      1.092600  0.016358  1.104145  0.016562       NaN      NaN  
63.AC      1.079160  0.017525  1.080281  0.017557       NaN      NaN  
64.AC      1.129327  0.018714  1.089272  0.018064       NaN      NaN  
65b.AC     1.000000         .  1.000000         .       NaN      NaN  
1926.coh   1.145954  0.015919  1.201885  0.016721       NaN      NaN  
1930.coh   1.087242  0.014004  1.113391   0.01435       NaN      NaN  
1935.coh   1.022441  0.013243  1.026395  0.013294       NaN      NaN  
1940b.coh  1.000000         .  1.000000         .       NaN      NaN  
1945.coh   0.962471  0.015508  0.955253  0.015394       NaN      NaN  
1950.coh   0.921920  0.023205  0.856464  0.021592       NaN      NaN  
0b.SEX     1.000000         .  1.000000         .       NaN      NaN  
1.SEX      1.978722  0.017109  1.887753  0.016448       NaN      NaN  
0b.imm_d   1.000000         .  1.000000         .       NaN      NaN  
1.imm_d    0.730600  0.010578  0.715829  0.010362       NaN      NaN  
0b.mrt     1.000000         .  1.000000         .       NaN      NaN  
1.mrt      0.756651  0.006585  0.816223  0.007218       NaN      NaN  
2.mrt      1.133791  0.033726  1.025032   0.03064       NaN      NaN  
1.p_lvl    1.314221  0.01594

## Compute the hazard rate for $t \in [-5,45]$

$ h(t)=\beta_{0}\prod(\beta_{j})\exp{(\gamma*t)} $, where

$\beta_{0}$ is the constant

$\beta_{j}$ is the hazard ratio of binary variable j

$\gamma$ is the gompertz parameter

$t$ is the time relative to 65 (so we compute for ages 60 to 110)

In [2]:
def get_hazard(in_df, out_df):
    #consider the 5 models imported separately
    for model in range(1, 6):
        model_name = f'b{model}'
        #extract the gamma and constant
        gamma = float(in_df.at['gamma', model_name])
        cons = float(in_df.at['_cons', model_name])
        
        #for each of our variable, 
        #extract the first characters of the index to know what level we are considering
        #extract the hazard ratio
        ac_values = [(index[:2], value) for index, value in in_df.loc[in_df.index.str.endswith('.AC'), model_name].items()]
        coh_values = [(index[:4], value) for index, value in in_df.loc[in_df.index.str.endswith('.coh'), model_name].items()]
        sex_values = [(index[:1], value) for index, value in in_df.loc[in_df.index.str.endswith('.SEX'), model_name].items()] if model_name in ['b2', 'b3', 'b4', 'b5'] else [(99, 1)]
        imm_values = [(index[:1], value) for index, value in in_df.loc[in_df.index.str.endswith('.imm_d'), model_name].items()] if model_name in ['b3', 'b4', 'b5'] else [(99, 1)]
        mrt_values = [(index[:1], value) for index, value in in_df.loc[in_df.index.str.endswith('.mrt'), model_name].items()] if model_name in ['b3', 'b4', 'b5'] else [(99, 1)]
        pen_values = [(index[:1], value) for index, value in in_df.loc[in_df.index.str.endswith('.p_lvl'), model_name].items()] if model_name in ['b4', 'b5'] else [(99, 1)]
        ppen_values = [(index[:1], value) for index, value in in_df.loc[in_df.index.str.endswith('.pp_lvl'), model_name].items()] if model_name == 'b5' else [(99, 1)]
        
        #define the age range we want to generate the hazard rate on
        t = np.arange(-5,46)
        #generate all possible combinations of values
        combinations = product(ac_values, coh_values, sex_values, imm_values, mrt_values, pen_values, ppen_values)
        for ac, coh, sex, imm, mrt, pen, ppen in combinations:
            #compute hazard rate
            fct = cons * ac[1] * coh[1] * sex[1] * imm[1] * mrt[1] * pen[1] * ppen[1] * np.exp(t * gamma)
            #store the characteristics used in computing and the hazard rate
            new_row = {'AC': ac[0], 'coh': coh[0], 'sex': sex[0], 'imm': imm[0], 'mrt': mrt[0], 'p': pen[0], 'pp': ppen[0], 't': t, 'ht': fct}
            #append stored estimates to the out dataframe
            out_df = out_df.append(new_row, ignore_index=True)
    return out_df

#initialize empty dataframe to receive out_df
hazard = pd.DataFrame(columns=['AC', 'coh', 'sex', 'imm', 'mrt', 'p', 'pp', 't', 'ht'])
#run the function
hazard = get_hazard(df, hazard)


C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ignore_index=True)
C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ignore_index=True)
C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ignore_index=True)
C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ign

C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ignore_index=True)
C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ignore_index=True)
C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ignore_index=True)
C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ign

C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ignore_index=True)
C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ignore_index=True)
C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ignore_index=True)
C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ign

C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ignore_index=True)
C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ignore_index=True)
C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ignore_index=True)
C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ign

C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ignore_index=True)
C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ignore_index=True)
C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ignore_index=True)
C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ign

...

C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ignore_index=True)
C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ignore_index=True)
C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ignore_index=True)
C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ign

C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ignore_index=True)
C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ignore_index=True)
C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ignore_index=True)
C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ign

C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ignore_index=True)
C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ignore_index=True)
C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ignore_index=True)
C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ign

C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ignore_index=True)
C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ignore_index=True)
C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ignore_index=True)
C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ign

C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ignore_index=True)
C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ignore_index=True)
C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ignore_index=True)
C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\1123459356.py:30: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ign

## Change the previous table which had the hazard rate saved as a list to a dataframe that has the hazard rate saved as a column with all characteristics used in computing

In [3]:
#initialize receiving df
table=pd.DataFrame()
#multiply all characteristics by 51 so that they are lists like the hazard rate
for var in ['AC','coh','sex','imm','mrt','p','pp']:
    hazard[var] = hazard[var].apply(lambda x: [x] * 51)
    table[var]=hazard[var].explode()
#explode all series into a long form dataframe    
table['t'] = hazard['t'].explode()
table['ht'] = hazard['ht'].explode()
table=table.reset_index()
#column identity serves to indicate separate combinations of characteristics used in computing hazard rate
table=table.rename(columns={'index':'identity'})
table.head(60)

identity  AC   coh sex imm mrt   p  pp   t        ht
0          0  60  1926  99  99  99  99  99  -5  0.005216
1          0  60  1926  99  99  99  99  99  -4  0.005853
2          0  60  1926  99  99  99  99  99  -3  0.006567
3          0  60  1926  99  99  99  99  99  -2  0.007367
4          0  60  1926  99  99  99  99  99  -1  0.008266
5          0  60  1926  99  99  99  99  99   0  0.009274
6          0  60  1926  99  99  99  99  99   1  0.010405
7          0  60  1926  99  99  99  99  99   2  0.011675
8          0  60  1926  99  99  99  99  99   3  0.013098
9          0  60  1926  99  99  99  99  99   4  0.014696
10         0  60  1926  99  99  99  99  99   5  0.016488
11         0  60  1926  99  99  99  99  99   6    0.0185
12         0  60  1926  99  99  99  99  99   7  0.020756
13         0  60  1926  99  99  99  99  99   8  0.023287
14         0  60  1926  99  99  99  99  99   9  0.026128
15         0  60  1926  99  99  99  99  99  10  0.029314
16         0  60  1926  99  99  99  99  99  11   0.03289
17         0  60  1926  99  99  99  99  99  12  0.036901
18         0  60  1926  99  99  99  99  99  13  0.041402
19         0  60  1926  99  99  99  99  99  14  0.046452
20         0  60  1926  99  99  99  99  99  15  0.052118
21         0  60  1926  99  99  99  99  99  16  0.058474
22         0  60  1926  99  99  99  99  99  17  0.065606
23         0  60  1926  99  99  99  99  99  18  0.073608
24         0  60  1926  99  99  99  99  99  19  0.082586
25         0  60  1926  99  99  99  99  99  20  0.092659
26         0  60  1926  99  99  99  99  99  21   0.10396
27         0  60  1926  99  99  99  99  99  22   0.11664
28         0  60  1926  99  99  99  99  99  23  0.130867
29         0  60  1926  99  99  99  99  99  24  0.146828
30         0  60  1926  99  99  99  99  99  25  0.164736
31         0  60  1926  99  99  99  99  99  26  0.184829
32         0  60  1926  99  99  99  99  99  27  0.207372
33         0  60  1926  99  99  99  99  99  28  0.232665
34         0  60  1926  99  99  99  99  99  29  0.261043
35         0  60  1926  99  99  99  99  99  30  0.292881
36         0  60  1926  99  99  99  99  99  31  0.328604
37         0  60  1926  99  99  99  99  99  32  0.368683
38         0  60  1926  99  99  99  99  99  33   0.41365
39         0  60  1926  99  99  99  99  99  34  0.464102
40         0  60  1926  99  99  99  99  99  35  0.520708
41         0  60  1926  99  99  99  99  99  36  0.584218
42         0  60  1926  99  99  99  99  99  37  0.655474
43         0  60  1926  99  99  99  99  99  38   0.73542
44         0  60  1926  99  99  99  99  99  39  0.825118
45         0  60  1926  99  99  99  99  99  40  0.925756
46         0  60  1926  99  99  99  99  99  41  1.038669
47         0  60  1926  99  99  99  99  99  42  1.165353
48         0  60  1926  99  99  99  99  99  43  1.307489
49         0  60  1926  99  99  99  99  99  44  1.466961
50         0  60  1926  99  99  99  99  99  45  1.645883
51         1  60  1930  99  99  99  99  99  -5  0.004775
52         1  60  1930  99  99  99  99  99  -4  0.005357
53         1  60  1930  99  99  99  99  99  -3   0.00601
54         1  60  1930  99  99  99  99  99  -2  0.006743
55         1  60  1930  99  99  99  99  99  -1  0.007566
56         1  60  1930  99  99  99  99  99   0  0.008489
57         1  60  1930  99  99  99  99  99   1  0.009524
58         1  60  1930  99  99  99  99  99   2  0.010686
59         1  60  1930  99  99  99  99  99   3  0.011989

## Compute lx and dx

$lx_{-5}=N_{-5}$

$lx_{t}=lx_{t-1}-dx_{t}, \forall t>-5$

$dx_{t}=lx_{t}*h(t)$

In [4]:
# Get initial lx value (t=0)
initial_lx = df['N'].values[0]

# Initialize lx and dx lists to store calculated values
lx_values = []
dx_values = []

# Iterate through each row in the DataFrame
for index, row in table.iterrows():
    t = row['t']
    if t == -5:
        lx=initial_lx
    else:
        # Calculate lx for t>60
        lx = lx_values[-1] - dx_values[-1]
    ht = row['ht']
    dx = lx * ht
    #append calculated values to the lists
    dx_values.append(dx)
    lx_values.append(lx)


# Update 'lx' and 'dx' columns in the DataFrame
table['lx'] = lx_values
table['dx'] = dx_values

## Compute Lx

$Lx_{-5}=\frac{lx_{-5}+lx_{-4}}{2}$

$Lx_{t}=Lx_{t-1}-dx_{t}$


In [5]:
Lx_values = []

# Iterate through each row in the DataFrame
for index, row in table.iterrows():
    t = row['t']
    lx = row['lx']
    dx = row['dx']
    if t == -5:
        #for the first year, Lx is the average of Lx at t=0 and t=1
        Lx =(lx + table.iloc[index+1]['lx'])/2
    else:
        # Calculate Lx for other t
        Lx = Lx_values[-1] - dx
    Lx_values.append(Lx)


# Update 'Lx' columns in the DataFrame
table['Lx'] = Lx_values

## Compute Tx as cumsum of Lx
$ Tx_{k}=\sum_{t=k}^{50}Lx_{k}$

In [6]:
#Tx

group=table.groupby('identity')
tx_group = group['Lx'].apply(lambda x: x[::-1].cumsum()[::-1])
table['Tx']=tx_group

C:\Users\Xavier\AppData\Local\Temp\ipykernel_4632\89395087.py:4: FutureWarning: Not prepending group keys to the result index of transform-like apply. In the future, the group keys will be included in the index, regardless of whether the applied function returns a like-indexed object.
To preserve the previous behavior, use

	>>> .groupby(..., group_keys=False)

To adopt the future behavior and silence this warning, use 

	>>> .groupby(..., group_keys=True)
  tx_group = group['Lx'].apply(lambda x: x[::-1].cumsum()[::-1])


## Compute expected lifespan
$ex=\frac{Tx}{Lx}$

In [7]:
#expected lifespan
table['ex']=table['Tx']/table['Lx']

table.head(5)

identity  AC   coh sex imm mrt   p  pp   t        ht             lx  \
0         0  60  1926  99  99  99  99  99  -5  0.005216  307055.000000   
1         0  60  1926  99  99  99  99  99  -4  0.005853  305453.262345   
2         0  60  1926  99  99  99  99  99  -3  0.006567  303665.538405   
3         0  60  1926  99  99  99  99  99  -2  0.007367  301671.508472   
4         0  60  1926  99  99  99  99  99  -1  0.008266  299448.961563   

            dx             Lx            Tx         ex  
0  1601.737655  306254.131173  7.094105e+06  23.164112  
1  1787.723940  304466.407232  6.787851e+06  22.294252  
2  1994.029933  302472.377300  6.483384e+06  21.434633  
3  2222.546909  300249.830390  6.180912e+06  20.585897  
4  2475.254900  297774.575491  5.880662e+06  19.748705

## Isolate expected lifespan at 60 and 65

In [9]:
# Check if values in 't' column are equal to -5
mask60 = table['t'] == -5
mask65 = table['t'] == 0

# Assign values from 'ex' column to 'ex60' column where 't' equals -5
table.loc[mask60, 'ex60'] = table.loc[mask60, 'ex']
table.loc[mask65, 'ex65'] = table.loc[mask65, 'ex']
table['ex65']=table.groupby('identity')['ex65'].transform('max')
table.head(10)

identity  AC   coh sex imm mrt   p  pp   t        ht             lx  \
0         0  60  1926  99  99  99  99  99  -5  0.005216  307055.000000   
1         0  60  1926  99  99  99  99  99  -4  0.005853  305453.262345   
2         0  60  1926  99  99  99  99  99  -3  0.006567  303665.538405   
3         0  60  1926  99  99  99  99  99  -2  0.007367  301671.508472   
4         0  60  1926  99  99  99  99  99  -1  0.008266  299448.961563   
5         0  60  1926  99  99  99  99  99   0  0.009274  296973.706663   
6         0  60  1926  99  99  99  99  99   1  0.010405  294219.505905   
7         0  60  1926  99  99  99  99  99   2  0.011675  291158.039259   
8         0  60  1926  99  99  99  99  99   3  0.013098  287758.912716   
9         0  60  1926  99  99  99  99  99   4  0.014696  283989.724652   

            dx             Lx            Tx         ex       ex60       ex65  
0  1601.737655  306254.131173  7.094105e+06  23.164112  23.164112  18.923736  
1  1787.723940  304466.407232  6.787851e+06  22.294252        NaN  18.923736  
2  1994.029933  302472.377300  6.483384e+06  21.434633        NaN  18.923736  
3  2222.546909  300249.830390  6.180912e+06  20.585897        NaN  18.923736  
4  2475.254900  297774.575491  5.880662e+06  19.748705        NaN  18.923736  
5  2754.200759  295020.374732  5.582888e+06  18.923736        NaN  18.923736  
6  3061.466646  291958.908086  5.287867e+06  18.111683        NaN  18.923736  
7  3399.126543  288559.781543  4.995908e+06  17.313252        NaN  18.923736  
8  3769.188064  284790.593479  4.707349e+06  16.529157        NaN  18.923736  
9  4173.516419  280617.077061  4.422558e+06  15.760117        NaN  18.923736

## Create final dataset, only containing characteristics used in computing expected lifespan and expected lifespan at 60

In [11]:
unique = table[table['ex60'].notna()]
df_final=pd.DataFrame()
df_final['AC']=unique['AC']
df_final['coh']=unique['coh']
df_final['sex']=unique['sex']
df_final['imm']=unique['imm']
df_final['mrt']=unique['mrt']
df_final['p']=unique['p']
df_final['pp']=unique['pp']
df_final['ex60']=unique['ex60']
df_final['ex65']=unique['ex65']
df_final=df_final.reset_index()
del df_final['index']
df_final

AC   coh sex imm mrt   p  pp       ex60       ex65
0      60  1926  99  99  99  99  99  23.164112  18.923736
1      60  1930  99  99  99  99  99  23.831924  19.549224
2      60  1935  99  99  99  99  99  24.561232  20.234942
3      60  1940  99  99  99  99  99  24.802196  20.462080
4      60  1945  99  99  99  99  99  25.161254  20.801043
...    ..   ...  ..  ..  ..  ..  ..        ...        ...
15655  65  1950   1   1   2   5   1  25.966239  21.508763
15656  65  1950   1   1   2   5   2  26.271528  21.799216
15657  65  1950   1   1   2   5   3  26.491113  22.008370
15658  65  1950   1   1   2   5   4  26.754647  22.259648
15659  65  1950   1   1   2   5   5  28.799741  24.218629

[15660 rows x 9 columns]

In [12]:
for num in '60', '65':
    filter = (df_final[
    (df_final['AC'] == num) &       # 60 61 62 63 64 65
    (df_final['coh'] == '1950') &   # 1926 1930 1935 1940 1945 1950
    (df_final['sex'] == '1') &      # 0(w) 1(m) No
    (df_final['imm'] == '1') &      # 0(no) 1(yes) No
    (df_final['mrt'] == '1') &      # 0(div/single) 1(marr) 2(widow) No
    (df_final['p'] == '3') &        # 1 2 3 4 5 No
    (df_final['pp'] == '1')])       # 0(no) 1 2 3 4 5 No
    if num=='60':
        sum_60 = filter['ex60'].describe().loc['mean']
    elif num=='65':
        sum_65 = filter['ex60'].describe().loc['mean']
print("Expected lifespan when claiming: @ 60 =",round(sum_60,2), "@65 =", round(sum_65,2))

Expected lifespan when claiming: @ 60 = 26.45 @65 = 27.77


In [13]:
df_final.to_csv('../data/ex_no_dis.csv')